# Graph Coloring with Physics-Inspired Graph Neural Networks

In this notebook we show how to solve graph coloring problems with physics-inspired graph neural networks, as outlined in Martin J. A. Schuetz, J. Kyle Brubaker, Zhihuai Zhu, Helmut G. Katzgraber, _Graph Coloring with Physics-Inspired Graph Neural Networks_, [arXiv:2202.01606](https://arxiv.org/abs/2202.01606). 
Here we solve one example COLOR graph problem, but our approach can easily be extended to other problems, for instance the citations graphs. 
For the implementation of the graph neural network layers (GraphConv, GraphSAGE, etc) we use the open-source [```dgl``` library](https://github.com/dmlc/dgl/tree/0.9.x). 

Please note we have provided a `requirements.txt` file, which defines the environment required to run this code. Because some of the packages are not available on default OSX conda channels, we have also provided suggested channels to find them on. These can be distilled into a single line as such:

> conda create -n \<environment_name\> python=3.7 --file requirements.txt -c dglteam

## Preliminaries

1. 
We include logic to determine whether to use CUDA (e.g. GPU) or CPU backend, but it's important to note that DGL library must be installed with CUDA drivers included or this script will fail. We include comments in `requirements.txt` on how to handle this, which we reproduce here for visibility:

```
# For CPU-based DGL installation (default option):
dgl

# For GPU-based DGL installation:
# DGL installation is complicated if you want to include CUDA (i.e. use GPUs)
# First, go to the terminal and look for the CUDA version, i.e. via `nvidia-smi`
# With that version, you can insert into the following command:
# `conda install -c dglteam dgl-cudaXY.Z`
# For instance, if CUDA version = 11.0:
# `conda install -c dglteam dgl-cuda11.0`
#dgl-cuda11.0

```

2. 
To help keep repository size low, we do not include the input dataset but provide command lines to download and unzip data files. The COLOR dataset can be downloaded from this site: https://mat.tepper.cmu.edu/COLOR/instances.html

    The direct download link to the `instances.tar` object is here: https://mat.tepper.cmu.edu/COLOR/instances/instances.tar

    We suggest downloading these files under the parent path `data/input/COLOR` and unpacking there, such that you have `queen5_5.col` and the path `data/input/COLOR/instances/queen5_5.col`. However, this is left to the user, and the parent path to file `queen5_5.col` (or whichever specific problem the user chooses) can be specified in the `input_parent` variable in **cell 3**
    
    You can unpack the tar file via any standard utility (i.e. by double-clicking on it) or via command line, such as (on linux) `tar -xvf instances.tar`

# Set Up Environment

In [1144]:
import random
import torch
import warnings
import numpy as np
import networkx as nx
import os
import dgl
import networkx as nx
from parser import FileParser
import string
import random
from time import time


warnings.filterwarnings('ignore')

path_to_file = "./datasets/"
file_name = 'test_instance_7'
file_parser = FileParser(path_to_file, file_name + ".dat")
flows, distances, num_nodes = file_parser.parse_file()

In [1145]:
def generate_distance_matrix(n):
    """
    Generates a symmetric matrix of size n x n.
    
    :param n: Size of the matrix.
    :return: A symmetric matrix represented as a list of lists.
    """
    # Initialize an empty n x n matrix.
    matrix = [[0] * n for _ in range(n)]
    
    # Fill the lower triangular part of the matrix with random values.
    for i in range(n):
        for j in range(i + 1):
            matrix[i][j] = random.randint(1, 10)  # You can adjust the range of random values as needed.
    
    # Copy the elements from the lower triangular part to the upper triangular part.
    for i in range(n):
        for j in range(i + 1, n):
            matrix[i][j] = matrix[j][i]

    # making diagonal elements 0
    for i in range(n):
            matrix[i][i] = 0
    
    
    return np.array(matrix)

def generate_flow_matrix(n):
    """
    Generates a symmetric matrix of size n x n.
    
    :param n: Size of the matrix.
    :return: A symmetric matrix represented as a list of lists.
    """
    # Initialize an empty n x n matrix.
    matrix = [[0] * n for _ in range(n)]
    
    # Fill the lower triangular part of the matrix with random values.
    for i in range(n):
        for j in range(i + 1):
            matrix[i][j] = random.randint(0, 5)  # You can adjust the range of random values as needed.
    
    # Copy the elements from the lower triangular part to the upper triangular part.
    for i in range(n):
        for j in range(i + 1, n):
            matrix[i][j] = matrix[j][i]
    
    # making diagonal elements 0
    for i in range(n):
            matrix[i][i] = 0
    
    return np.array(matrix)

n = 4

distances = generate_distance_matrix(n)
flows = generate_distance_matrix(n)

In [1146]:
import networkx as nx
import torch
import torch.nn as nn
import torch.nn.functional as F
import random
import numpy as np
import os
from dgl.nn.pytorch import SAGEConv
from dgl.nn.pytorch import GraphConv
from itertools import chain
import math


# Known chromatic numbers for specified problems (from references)
chromatic_numbers = {
    # COLOR graphs
    'jean.col': 10,
    'anna.col': 11,
    'huck.col': 11,
    'david.col': 11,
    'homer.col': 13,
    'myciel5.col': 6,
    'myciel6.col': 7,
    'queen5_5.col': 5,
    'queen6_6.col': 7,
    'queen7_7.col': 7,
    'queen8_8.col': 9,
    'queen9_9.col': 10,
    'queen8_12.col': 12,
    'queen11_11.col': 11,
    'queen13_13.col': 13,
    # Citations graphs
    'cora.cites': 5,
    'citeseer.cites': 6,
    'pubmed.cites': 8
}




def set_seed(seed):
    """
    Sets random seeds for training.

    :param seed: Integer used for seed.
    :type seed: int
    """
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    if torch.cuda.is_available():
        torch.cuda.manual_seed_all(seed)


def get_adjacency_matrix(nx_graph, torch_device, torch_dtype):
    """
    Pre-load adjacency matrix, map to torch device

    :param nx_graph: Graph object to pull adjacency matrix for
    :type nx_graph: networkx.OrderedGraph
    :param torch_device: Compute device to map computations onto (CPU vs GPU)
    :type torch_dtype: str
    :param torch_dtype: Specification of pytorch datatype to use for matrix
    :type torch_dtype: str
    :return: Adjacency matrix for provided graph
    :rtype: torch.tensor
    """

    adj = nx.linalg.graphmatrix.adjacency_matrix(nx_graph).todense()
    adj_ = torch.tensor(adj).type(torch_dtype).to(torch_device)

    return adj_


def parse_line(file_line, node_offset):
    """
    Helper function to parse lines out of COLOR files - skips first character, which
    will be an "e" to denote an edge definition, and returns node0, node1 that define
    the edge in the line.

    :param file_line: Line to be parsed
    :type file_line: str
    :param node_offset: How much to add to account for file numbering (i.e. offset by 1)
    :type node_offset: int
    :return: Set of nodes connected by edge defined in the line (i.e. node_from, node_to)
    :rtype: int, int
    """

    x, y = file_line.split(' ')[1:]  # skip first character - specifies each line is an edge definition
    x, y = int(x)+node_offset, int(y)+node_offset  # nodes in file are 1-indexed, whereas python is 0-indexed
    return x, y


def build_graph_from_color_file(fname, node_offset=-1, parent_fpath=''):
    """
    Load problem definition (graph) from COLOR file (e.g. *.col).

    :param fname: Filename of COLOR file
    :type fname: str
    :param node_offset: How much to offset node values contained in file
    :type node_offset: int
    :param parent_fpath: Path to prepend to `fname`
    :type parent_fpath: str
    :return: Graph defined in provided file
    :rtype: networkx.OrderedGraph
    """

    fpath = os.path.join(parent_fpath, fname)

    print(f'Building graph from contents of file: {fpath}')
    with open(fpath, 'r') as f:
        content = f.read().strip()

    # Identify where problem definition starts.
    # All lines prior to this are assumed to be miscellaneous descriptions of file contents
    # which start with "c ".
    start_idx = [idx for idx, line in enumerate(content.split('\n')) if line.startswith('p')][0]
    lines = content.split('\n')[start_idx:]  # skip comment line(s)
    edges = [parse_line(line, node_offset) for line in lines[1:] if len(line) > 0]

    nx_temp = nx.from_edgelist(edges)

    nx_graph = nx.Graph()
    nx_graph.add_nodes_from(sorted(nx_temp.nodes()))
    nx_graph.add_edges_from(nx_temp.edges)

    return nx_graph



# Generate random graph of specified size and type,
# with specified degree (d) or edge probability (p)
def generate_graph(file_name, graph_type='reg', random_seed=0):
    """
    Helper function to generate a NetworkX random graph of specified type,
    given specified parameters (e.g. d-regular, d=3). Must provide one of
    d or p, d with graph_type='reg', and p with graph_type in ['prob', 'erdos'].

    Input:
        n: Problem size
        d: [Optional] Degree of each node in graph
        p: [Optional] Probability of edge between two nodes
        graph_type: Specifies graph type to generate
        random_seed: Seed value for random generator
    Output:
        nx_graph: NetworkX OrderedGraph of specified type and parameters
    """


    p = None
    n = distances.shape[0]
    d = n-1


    if graph_type == 'reg':
        print(f'Generating d-regular graph with n={n}, d={d}, seed={random_seed}')
        nx_temp = nx.random_regular_graph(d=d, n=n, seed=random_seed)
    elif graph_type == 'prob':
        print(f'Generating p-probabilistic graph with n={n}, p={p}, seed={random_seed}')
        nx_temp = nx.fast_gnp_random_graph(n, p, seed=random_seed)
    elif graph_type == 'erdos':
        print(f'Generating erdos-renyi graph with n={n}, p={p}, seed={random_seed}')
        nx_temp = nx.erdos_renyi_graph(n, p, seed=random_seed)
    else:
        raise NotImplementedError(f'!! Graph type {graph_type} not handled !!')

    # Networkx does not enforce node order by default
    nx_temp = nx.relabel.convert_node_labels_to_integers(nx_temp)
    # Need to pull nx graph into OrderedGraph so training will work properly
    nx_graph = nx.Graph()
    nx_graph.add_nodes_from(sorted(nx_temp.nodes()))
    nx_graph.add_edges_from(nx_temp.edges)
    return nx_graph


# Define GNN GraphSage object
class GNNSage(nn.Module):
    """
    Basic GraphSAGE-based GNN class object. Constructs the model architecture upon
    initialization. Defines a forward step to include relevant parameters - in this
    case, just dropout.
    """

    def __init__(self, g, in_feats, hidden_size, num_classes, dropout, agg_type='mean'):
        """
        Initialize the model object. Establishes model architecture and relevant hypers (`dropout`, `num_classes`, `agg_type`)

        :param g: Input graph object
        :type g: dgl.DGLHeteroGraph
        :param in_feats: Size (number of nodes) of input layer
        :type in_feats: int
        :param hidden_size: Size of hidden layer
        :type hidden_size: int
        :param num_classes: Size of output layer (one node per class)
        :type num_classes: int
        :param dropout: Dropout fraction, between two convolutional layers
        :type dropout: float
        :param agg_type: Aggregation type for each SAGEConv layer. All layers will use the same agg_type
        :type agg_type: str
        """
        
        super(GNNSage, self).__init__()

        self.g = g
        self.num_classes = num_classes
        
        self.layers = nn.ModuleList()
        # input layer
        self.layers.append(SAGEConv(in_feats, hidden_size, agg_type, activation=F.relu))
        # output layer
        self.layers.append(SAGEConv(hidden_size, num_classes, agg_type))
        self.dropout = nn.Dropout(p=dropout)

    def forward(self, features):
        """
        Define forward step of netowrk. In this example, pass inputs through convolution, apply relu
        and dropout, then pass through second convolution.

        :param features: Input node representations
        :type features: torch.tensor
        :return: Final layer representation, pre-activation (i.e. class logits)
        :rtype: torch.tensor
        """
        h = features
        for i, layer in enumerate(self.layers):
            if i != 0:
                h = self.dropout(h)
            h = layer(self.g, h)

        return h


# Define GNN GraphConv object
class GNNConv(nn.Module):
    """
    Basic GraphConv-based GNN class object. Constructs the model architecture upon
    initialization. Defines a forward step to include relevant parameters - in this
    case, just dropout.
    """
    
    def __init__(self, g, in_feats, hidden_size, num_classes, dropout):
        """
        Initialize the model object. Establishes model architecture and relevant hypers (`dropout`, `num_classes`, `agg_type`)

        :param g: Input graph object
        :type g: dgl.DGLHeteroGraph
        :param in_feats: Size (number of nodes) of input layer
        :type in_feats: int
        :param hidden_size: Size of hidden layer
        :type hidden_size: int
        :param num_classes: Size of output layer (one node per class)
        :type num_classes: int
        :param dropout: Dropout fraction, between two convolutional layers
        :type dropout: float
        """
        
        super(GNNConv, self).__init__()
        self.g = g
        self.layers = nn.ModuleList()
        # input layer
        self.layers.append(GraphConv(in_feats, hidden_size, activation=F.relu))
        # output layer
        self.layers.append(GraphConv(hidden_size, num_classes))
        self.dropout = nn.Dropout(p=dropout)

    def forward(self, features):
        """
        Define forward step of netowrk. In this example, pass inputs through convolution, apply relu
        and dropout, then pass through second convolution.

        :param features: Input node representations
        :type features: torch.tensor
        :return: Final layer representation, pre-activation (i.e. class logits)
        :rtype: torch.tensor
        """
            
        h = features
        for i, layer in enumerate(self.layers):
            if i != 0:
                h = self.dropout(h)
            h = layer(self.g, h)
        return h


# Construct graph to learn on #
def get_gnn(g, n_nodes, gnn_hypers, opt_params, torch_device, torch_dtype):
    """
    Helper function to load in GNN object, optimizer, and initial embedding layer.

    :param n_nodes: Number of nodes in graph
    :type n_nodes: int
    :param gnn_hypers: Hyperparameters to provide to GNN constructor
    :type gnn_hypers: dict
    :param opt_params: Hyperparameters to provide to optimizer constructor
    :type opt_params: dict
    :param torch_device: Compute device to map computations onto (CPU vs GPU)
    :type torch_dtype: str
    :param torch_dtype: Specification of pytorch datatype to use for matrix
    :type torch_dtype: str
    :return: Initialized GNN instance, embedding layer, initialized optimizer instance
    :rtype: GNN_Conv or GNN_SAGE, torch.nn.Embedding, torch.optim.AdamW
    """

    try:
        print(f'Function get_gnn(): Setting seed to {gnn_hypers["seed"]}')
        set_seed(gnn_hypers['seed'])
    except KeyError:
        print('!! Function get_gnn(): Seed not specified in gnn_hypers object. Defaulting to 0 !!')
        set_seed(0)

    model = gnn_hypers['model']
    dim_embedding = gnn_hypers['dim_embedding']
    hidden_dim = gnn_hypers['hidden_dim']
    dropout = gnn_hypers['dropout']
    number_classes = gnn_hypers['number_classes']
    agg_type = gnn_hypers['layer_agg_type'] or 'mean'

    # instantiate the GNN
    print(f'Building {model} model...')
    if model == "GraphConv":
        net = GNNConv(g, dim_embedding, hidden_dim, number_classes, dropout)
    elif model == "GraphSAGE":
        net = GNNSage(g, dim_embedding, hidden_dim, number_classes, dropout, agg_type)
    else:
        raise ValueError("Invalid model type input! Model type has to be in one of these two options: ['GraphConv', 'GraphSAGE']")

    net = net.type(torch_dtype).to(torch_device)
    embed = nn.Embedding(n_nodes, dim_embedding)
    embed = embed.type(torch_dtype).to(torch_device)

    # set up Adam optimizer
    params = chain(net.parameters(), embed.parameters())

    print('Building ADAM-W optimizer...')
    optimizer = torch.optim.AdamW(params, **opt_params, weight_decay=1e-2)

    return net, embed, optimizer


def scale_array(arr):
    """
    Scales a NumPy array so that its elements are in the range [0, 1].

    Parameters:
    arr (np.ndarray): The input array.

    Returns:
    np.ndarray: The scaled array.
    """
    min_val = np.min(arr)
    max_val = np.max(arr)
    
    # Avoid division by zero if max_val equals min_val
    if max_val == min_val:
        return np.zeros_like(arr)
    
    scaled_arr = (arr - min_val) / (max_val - min_val)
    return scaled_arr

def scale_tensor(tensor):
    """
    Scales a PyTorch tensor so that its elements are in the range [0, 1].

    Parameters:
    tensor (torch.Tensor): The input tensor.

    Returns:
    torch.Tensor: The scaled tensor.
    """
    min_val = torch.min(tensor)
    max_val = torch.max(tensor)
    
    # Avoid division by zero if max_val equals min_val
    if max_val == min_val:
        return torch.zeros_like(tensor)
    
    scaled_tensor = (tensor - min_val) / (max_val - min_val)
    return scaled_tensor

def scale_value(l):
    """
    Scales the value l from the range [0, (n^2)*(n-1)^2/2] to the range [0, (n^3)/2].

    Parameters:
    l (float): The input value to be scaled, should be in the range [0, (n^2)*(n-1)^2/2].
    n (int): The parameter n used for scaling.

    Returns:
    float: The scaled value.

    
    """

    n = distances.shape[0]

    if n <= 1:
        raise ValueError("n should be greater than 1")
    if l < 0 or l > ((n**2)*(n-1)**2)/2:
        raise ValueError("l should be in the range [0, (n^2)*(n-1)^2/2]")
    
    l_scaled = l * (n / ((n - 1)**2))
    return l_scaled


# helper function for graph-coloring loss
def loss_func_mod(probs, adj_tensor):
    """
    Function to compute cost value based on soft assignments (probabilities)

    :param probs: Probability vector, of each node belonging to each class
    :type probs: torch.tensor
    :param adj_tensor: Adjacency matrix, containing internode weights
    :type adj_tensor: torch.tensor
    :return: Loss, given the current soft assignments (probabilities)
    :rtype: float
    """


    #print(adj_tensor.shape)
    flows_s = scale_array(flows)
    distances_s = scale_array(distances)
    probs_s = probs#scale_tensor(probs)

    loss1_ = 0
    for i in range(distances_s.shape[0]):
        for j in range(i+1,distances_s.shape[1]):
            d = distances_s[i,j]
            for k in range(flows_s.shape[0]):
                for l in range(k+1,flows_s.shape[1]):
                    f= flows_s[k,l]
                    p = probs_s[i,k]*probs_s[j,l] + probs_s[i,l]*probs_s[j,k]
                    loss1_ += d*f*p
    
    loss1_ = scale_value(loss1_)





    # Multiply probability vectors, then filter via elementwise application of adjacency matrix.
    #Divide by 2 to adjust for symmetry about the diagonal
    loss_ = torch.mul(adj_tensor, (probs @ probs.T)).sum() / 2  

    print('similarity loss '+ str(loss_) +  ' flow loss ' + str(loss1_)) 

    final_loss = loss_ + loss1_

    return final_loss



# helper function for custom loss according to Q matrix
def loss_func_color_hard(coloring, nx_graph):
    """
    Function to compute cost value based on color vector (0, 2, 1, 4, 1, ...)

    :param coloring: Vector of class assignments (colors)
    :type coloring: torch.tensor
    :param nx_graph: Graph to evaluate classifications on
    :type nx_graph: networkx.OrderedGraph
    :return: Cost of provided class assignments
    :rtype: torch.tensor
    """

    flows_s = scale_array(flows)
    distances_s = scale_array(distances)

    cost_ = 0
    max_d = np.max(distances_s)
    max_f = np.max(flows_s)
    n_edge = nx_graph.number_of_edges()

    for (u, v) in nx_graph.edges:
        cost_ += distances_s[u,v] *flows_s[coloring[u], coloring[v]] + n_edge*max_d*max_f*(coloring[u] == coloring[v])
    '''
    for (u, v) in nx_graph.edges:
        cost_ += 1*(coloring[u] == coloring[v])*(u != v)
    '''

    return cost_


def run_gnn_training(nx_graph, graph_dgl, adj_mat, net, embed, optimizer,
                     number_epochs=int(1e5), patience=1000, tolerance=1e-4, seed=1):
    """
    Function to run model training for given graph, GNN, optimizer, and set of hypers.
    Includes basic early stopping criteria. Prints regular updates on progress as well as
    final decision.

    :param nx_graph: Graph instance to solve
    :param graph_dgl: Graph instance to solve
    :param adj_mat: Adjacency matrix for provided graph
    :type adj_mat: torch.tensor
    :param net: GNN instance to train
    :type net: GNN_Conv or GNN_SAGE
    :param embed: Initial embedding layer
    :type embed: torch.nn.Embedding
    :param optimizer: Optimizer instance used to fit model parameters
    :type optimizer: torch.optim.AdamW
    :param number_epochs: Limit on number of training epochs to run
    :type number_epochs: int
    :param patience: Number of epochs to wait before triggering early stopping
    :type patience: int
    :param tolerance: Minimum change in cost to be considered non-converged (i.e.
        any change less than tolerance will add to early stopping count)
    :type tolerance: float

    :return: Final model probabilities, best color vector found during training, best loss found during training,
    final color vector of training, final loss of training, number of epochs used in training
    :rtype: torch.tensor, torch.tensor, torch.tensor, torch.tensor, torch.tensor, int
    """

    # Ensure RNG seeds are reset each training run
    print(f'Function run_gnn_training(): Setting seed to {seed}')
    set_seed(seed)

    inputs = embed.weight

    # Tracking
    best_cost = torch.tensor(float('Inf'))  # high initialization
    best_loss = torch.tensor(float('Inf'))
    best_coloring = None

    # Early stopping to allow NN to train to near-completion
    prev_loss = 1.  # initial loss value (arbitrary)
    cnt = 0  # track number times early stopping is triggered

    # Training logic
    for epoch in range(number_epochs):

        # get soft prob assignments
        logits = net(inputs)

        # apply softmax for normalization
        probs = F.softmax(logits, dim=1)

        #print(probs.shape)

        # get cost value with POTTS cost function
        loss = loss_func_mod(probs, adj_mat)

        # get cost based on current hard class assignments
        # update cost if applicable
        coloring = torch.argmax(probs, dim=1)
        cost_hard = loss_func_color_hard(coloring, nx_graph)


        if cost_hard < best_cost:
            best_loss = loss
            best_cost = cost_hard
            best_coloring = coloring

        # Early stopping check
        # If loss increases or change in loss is too small, trigger
        if (abs(loss - prev_loss) <= tolerance) | ((loss - prev_loss) > 0):
            cnt += 1
        else:
            cnt = 0
        
        # update loss tracking
        prev_loss = loss

        if cnt >= patience:
            print(f'Stopping early on epoch {epoch}. Patience count: {cnt}')
            break

        # run optimization with backpropagation
        optimizer.zero_grad()  # clear gradient for step
        loss.backward()  # calculate gradient through compute graph
        optimizer.step()  # take step, update weights

        # tracking: print intermediate loss at regular interval
        if epoch % 1000 == 0:
            print('Epoch %d | Soft Loss: %.5f' % (epoch, loss.item()))
            print('Epoch %d | Discrete Cost: %.5f' % (epoch, cost_hard.item()))

    # Print final loss
    #print('Epoch %d | Final loss: %.5f' % (epoch, loss.item()))
    #print('Epoch %d | Lowest discrete cost: %.5f' % (epoch, best_cost))

    # Final coloring
    final_loss = loss
    final_coloring = torch.argmax(probs, 1)
    print(f'Final coloring: {final_coloring}, soft loss: {final_loss}')

    return probs, best_coloring, best_loss, final_coloring, final_loss, epoch

In [1147]:
# fix seed to ensure consistent results
SEED_VALUE = 0
random.seed(SEED_VALUE)        # seed python RNG
np.random.seed(SEED_VALUE)     # seed global NumPy RNG
torch.manual_seed(SEED_VALUE)  # seed torch RNG

# Set GPU/CPU
TORCH_DEVICE = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
TORCH_DTYPE = torch.float32
print(f'Will use device: {TORCH_DEVICE}, torch dtype: {TORCH_DTYPE}')

Will use device: cpu, torch dtype: torch.float32


# Step 0 - Download COLOR datasets

Uncomment the following cells to download all the COLOR datasets. This only needs to be done once.

In [1148]:
'''

input_data_path = './data/input/COLOR/instances'
if not os.path.exists(input_data_path):
   os.makedirs(input_data_path)

!wget https://mat.tepper.cmu.edu/COLOR/instances/instances.tar -P ./data/input/COLOR/

!tar -xvf ./data/input/COLOR/instances.tar -C './data/input/COLOR/instances'

'''

"\n\ninput_data_path = './data/input/COLOR/instances'\nif not os.path.exists(input_data_path):\n   os.makedirs(input_data_path)\n\n!wget https://mat.tepper.cmu.edu/COLOR/instances/instances.tar -P ./data/input/COLOR/\n\n!tar -xvf ./data/input/COLOR/instances.tar -C './data/input/COLOR/instances'\n\n"

# Step 1 - Set hyperparameters

We provide a default set of model hypers. Feel free to modify these as desired. 

We also include general parameters such as tolerance and patience for early stopping, the layer aggregation specification (`layer_agg_type`) for GraphSAGE, and some tracking of problem definition (problem name, chromatic number).

In [1149]:
# Sample hyperparameters
if TORCH_DEVICE.type == 'cpu':  # example with CPU
    '''
    hypers = {
        'model': 'GraphConv',   # set either with 'GraphConv' or 'GraphSAGE'. It cannot take other input
        'dim_embedding': 64,
        'dropout': 0.1,
        'learning_rate': 0.0001,
        'hidden_dim': 64,
        'seed': SEED_VALUE
    }
    '''
    hypers = {
        'model': 'GraphConv',   # set either with 'GraphConv' or 'GraphSAGE'. It cannot take other input
        'dim_embedding': 64,
        'dropout': 0.1,
        'learning_rate': 0.0001,
        'hidden_dim': 64,
        'seed': SEED_VALUE
    }
else:                           # example with GPU
    hypers = {
        'model': 'GraphSAGE',
        'dim_embedding': 77,
        'dropout': 0.3784,
        'learning_rate': 0.02988,
        'hidden_dim': 32,
        'seed': SEED_VALUE
    }

# Default meta parameters
solver_hypers = {
    'tolerance': 1e-3,           # Loss must change by more than tolerance, or add towards patience count###########################################################################
    'number_epochs': int(5e4),   # Max number training steps
    'patience': 500,             # Number early stopping triggers before breaking loop##############################################################################################
    'layer_agg_type': 'mean',    # How aggregate neighbors sampled within graphSAGE
    'number_classes': distances.shape[0]#############################################################################################################################################
}

# Combine into a single set
hypers.update(solver_hypers)

# Step 2 - Load in problem and create graph

Load in problem definition from specified path. Variables `input_parent` and `problem_file` should be defined appropriately in cell 3.

In [1150]:

graph_type = 'reg'

nx_graph = generate_graph("test_instance_9",graph_type=graph_type, random_seed=100)


# Get DGL graph from networkx graph
# Ensure relevant objects are placed onto proper torch device
dgl_graph = dgl.from_networkx(nx_graph)
dgl_graph = dgl_graph.to(TORCH_DEVICE)

Generating d-regular graph with n=4, d=3, seed=100


In [1151]:
'''
# Visualize graph
pos = nx.kamada_kawai_layout(nx_graph)
nx.draw(nx_graph, pos, with_labels=True, node_color=[[.7, .7, .7]])
'''

'\n# Visualize graph\npos = nx.kamada_kawai_layout(nx_graph)\nnx.draw(nx_graph, pos, with_labels=True, node_color=[[.7, .7, .7]])\n'

# Step 3 - Set up optimizer/GNN architecture

Instantiate optimizer and GNN objects with specified hypers.

In [1152]:
# Retrieve known optimizer hypers
opt_hypers = {
    'lr': hypers.get('learning_rate', None)
}

# Get adjacency matrix for use in calculations
adj_ = get_adjacency_matrix(nx_graph, TORCH_DEVICE, TORCH_DTYPE)

# See minimal_utils.py for description. Constructs GNN and optimizer objects from given hypers. 
# Initializes embedding layer to use as initial model input
net, embed, optimizer = get_gnn(dgl_graph, nx_graph.number_of_nodes(), hypers, opt_hypers, TORCH_DEVICE, TORCH_DTYPE)

Function get_gnn(): Setting seed to 0
Building GraphConv model...
Building ADAM-W optimizer...


# Step 4 - Run GNN training

In [1153]:
t_start = time()

probs, best_coloring, best_loss, final_coloring, final_loss, epoch_num = run_gnn_training(
    nx_graph, dgl_graph, adj_, net, embed, optimizer, hypers['number_epochs'], 
    hypers['patience'], hypers['tolerance'], seed=SEED_VALUE)

runtime_gnn = round(time() - t_start, 4)

# report results
print(f'GNN runtime: {runtime_gnn}s')

Function run_gnn_training(): Setting seed to 0
similarity loss tensor(2.0243, grad_fn=<DivBackward0>) flow loss tensor(0.8345, grad_fn=<MulBackward0>)
Epoch 0 | Soft Loss: 2.85884
Epoch 0 | Discrete Cost: 36.00000
similarity loss tensor(1.8285, grad_fn=<DivBackward0>) flow loss tensor(0.8341, grad_fn=<MulBackward0>)
similarity loss tensor(1.9283, grad_fn=<DivBackward0>) flow loss tensor(0.8352, grad_fn=<MulBackward0>)
similarity loss tensor(1.7358, grad_fn=<DivBackward0>) flow loss tensor(0.8592, grad_fn=<MulBackward0>)
similarity loss tensor(1.9243, grad_fn=<DivBackward0>) flow loss tensor(0.8253, grad_fn=<MulBackward0>)
similarity loss tensor(1.8507, grad_fn=<DivBackward0>) flow loss tensor(0.8354, grad_fn=<MulBackward0>)
similarity loss tensor(2.0122, grad_fn=<DivBackward0>) flow loss tensor(0.8376, grad_fn=<MulBackward0>)
similarity loss tensor(1.7335, grad_fn=<DivBackward0>) flow loss tensor(0.8373, grad_fn=<MulBackward0>)
similarity loss tensor(1.7964, grad_fn=<DivBackward0>) flo

# Step 5 - Post-process GNN results

Print the out cost of best solution (with minimum cost value) found during training.

In [1154]:
# check for color violations
best_cost_hard = loss_func_color_hard(best_coloring, nx_graph)

print(f'Best (hard) cost of coloring (n_class={hypers["number_classes"]}): {best_cost_hard}')

Best (hard) cost of coloring (n_class=4): 2.1111111640930176


In [1155]:
from itertools import combinations

cost_ = 0
for (u, v) in nx_graph.edges:    
    cost_ += distances[u,v]  * flows[best_coloring[u], best_coloring[v]] 
print(best_coloring)
print(cost_)

best_coloring2 = best_coloring.tolist()

# Create an empty dictionary to store the count of each element
element_count = {}

# Iterate through the list and count the occurrences of each element
for element in best_coloring2:
    if element in element_count:
        
        element_count[element] += 1
    else:
        element_count[element] = 1

# Iterate through the dictionary and find elements with count greater than 1
repeated_elements = {element: count for element, count in element_count.items() if count > 1}
wrong_results = (sum(repeated_elements.values()) - len(repeated_elements))/len(best_coloring)

tensor([3, 0, 1, 2])
190


In [1156]:
import numpy as np
from scipy.optimize import quadratic_assignment

# Define the flow matrix (A) and the distance matrix (B)

flow_matrix = np.array(flows)

distance_matrix = np.array(distances)

# Solve the QAP
result = quadratic_assignment(flow_matrix, distance_matrix)

# Print the result
print(result.col_ind)
print(result.fun/2)

[1 0 2 3]
200.0


In [1157]:
flows

array([[ 0,  4,  3,  2],
       [ 4,  0,  5, 10],
       [ 3,  5,  0,  5],
       [ 2, 10,  5,  0]])

In [1158]:
distances

array([[0, 7, 5, 7],
       [7, 0, 9, 5],
       [5, 9, 0, 8],
       [7, 5, 8, 0]])

In [1159]:
flows

array([[ 0,  4,  3,  2],
       [ 4,  0,  5, 10],
       [ 3,  5,  0,  5],
       [ 2, 10,  5,  0]])

In [1162]:
import pulp

def solve_qap(flow_matrix, distance_matrix):
    n = len(flow_matrix)
    
    # Define the Linear Program
    model = pulp.LpProblem("QAP", pulp.LpMinimize)
    
    # Define binary decision variables x_ij, representing whether facility i is assigned to location j
    x = pulp.LpVariable.dicts("x", (range(n), range(n)), cat='Binary')
    
    # Define the objective function
    model += pulp.lpSum(distance_matrix[i][j] * flow_matrix[k][l] * x[i][k] * x[j][l]
                        for i in range(n) for j in range(n) for k in range(n) for l in range(n))
    
    # Add constraints ensuring that each facility is assigned to exactly one location
    for i in range(n):
        model += pulp.lpSum(x[i][j] for j in range(n)) == 1
    
    # Add constraints ensuring that each location is assigned exactly one facility
    for j in range(n):
        model += pulp.lpSum(x[i][j] for i in range(n)) == 1
    
    # Solve the problem
    model.solve()
    
    # Check if a solution is found
    if pulp.LpStatus[model.status] != 'Optimal':
        return None
    
    # Extract the solution
    assignment = {i: j for i in range(n) for j in range(n) if pulp.value(x[i][j]) == 1}
    return assignment, pulp.value(model.objective)

# Example usage:
flow_matrix = [
    [0, 3, 0, 2],
    [3, 0, 0, 1],
    [0, 0, 0, 4],
    [2, 1, 4, 0]
]

distance_matrix = [
    [0, 22, 53, 53],
    [22, 0, 40, 62],
    [53, 40, 0, 55],
    [53, 62, 55, 0]
]

assignment, objective_value = solve_qap(flow_matrix, distance_matrix)
print("Assignment:", assignment)
print("Objective Value:", objective_value)


TypeError: Non-constant expressions cannot be multiplied